In [1]:
import os
import re
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import seaborn as sns

import nltk
from nltk.corpus import stopwords
from nltk.stem.porter import PorterStemmer


%matplotlib notebook

In [2]:
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to /home/pedro/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [4]:
dataset = "movie_review_dataset"

temp = []
for folder in os.listdir(dataset):
    folder = os.path.join(dataset, folder)
    if not folder.endswith(".txt"):
        for file in os.listdir(os.path.join(folder, 'pos')):
            with open(os.path.join(folder, 'pos', file), 'r', encoding='utf8') as f:
                text = f.read()
                temp.append([text, True])

        for file in os.listdir(os.path.join(folder, 'neg')):
            with open(os.path.join(folder, 'neg', file), 'r', encoding='utf8') as f:
                text = f.read()
                temp.append([text, False])
    break

In [5]:
df = pd.DataFrame(temp,columns=['Review', 'Sentiment']) 
df.head()

Review  Sentiment
0  It would be something to try and tell someone ...       True
1  I gave this show a chance because of Jaleel Wh...       True
2  How good is this film? Apparently, good enough...       True
3  This movie is great. Stylish, fun, good acting...       True
4  This is one of my most favorite movies of all ...       True

In [6]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 25000 entries, 0 to 24999
Data columns (total 2 columns):
Review       25000 non-null object
Sentiment    25000 non-null bool
dtypes: bool(1), object(1)
memory usage: 219.8+ KB


## Cleaning Text

In [7]:
corpus = []

for i in range(0, df.shape[0]):
    if i % 1000 == 0:
        print(i)
    
    # remove numbers and punctuations
    review = re.sub('[^a-zA-Z]', ' ', df['Review'][i])

    # lower cases
    review = review.lower()

    # steming and removing stopwords words 
    review = review.split()
    ps = PorterStemmer()
    review = [ps.stem(word) for word in review if not word in set(stopwords.words('english'))]
    review = ' '.join(review)
    corpus.append(review)

0
1000
2000
3000
4000
5000
6000
7000
8000
9000
10000
11000
12000
13000
14000
15000
16000
17000
18000
19000
20000
21000
22000
23000
24000


In [45]:
print(corpus[0])

would someth tri tell someon fata morgana simpli mayb herzog goe sahara desert nearbi villag film assort landscap local broadest stroke feat either surrend get form world around entir without stori bound certain aspect written poetri camera shoot supposedli discard film stock wander like pure travelogu one might even jump easi conclus put immens landscap move rough civil cultur though actual normal cultur point level abstract abl convey properli sometim take get along close puriti creation section puriti part manipul either natur broken machin soon narrat read popol vuh way music film gradual process actual highli styliz shot add whole differ level hybrid film easi reward best come closest herzog idea ecstat truth imag whole career br br one wonder imag end time second section paradis lead along word spoken way around eye move along still pan word close religi write also music choic bizarr spare sing low key classic music goe togeth leonard cohen blind faith think side end compliment s

In [44]:
df['Review'][0]

'It would be something to try and tell someone what Fata Morgana is very simply about. Or, maybe it isn\'t: Herzog goes to the Sahara desert and nearby villages to film assorted landscapes and the locals. But this is just the broadest stroke. It\'s a feat that you either surrender yourself to, or you don\'t. He gets into the form of the world around him entirely, without a story, bound only to certain aspects of written poetry, as his camera (shooting on supposedly discarded film stock) wanders like in a pure travelogue. One might even jump to that easy conclusion, as he puts up these immense landscapes, then moving to more rough civilized culture (though not the actual \'normal\' culture itself), and to a point levels too abstract to be able to convey properly here. Sometimes it takes a while to get along, close to a purity through the "creation" section, but a purity in how parts are manipulated either by nature or by broken-down machines. Soon the narration, readings from the Popol 

## Creating the Bag of Words model

In [8]:
from sklearn.feature_extraction.text import CountVectorizer

cv = CountVectorizer(max_features=1500)
X = cv.fit_transform(corpus).toarray()
y = df.iloc[:, 1].values

## Split data

In [32]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.2)

In [50]:
len(X_train)

20000

In [51]:
len(X_test)

5000

## Decision Tree Model

In [55]:
from sklearn.tree import DecisionTreeClassifier
classifier = DecisionTreeClassifier(criterion = 'entropy')
classifier.fit(X_train, y_train)

DecisionTreeClassifier(class_weight=None, criterion='entropy', max_depth=None,
            max_features=None, max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=1, min_samples_split=2,
            min_weight_fraction_leaf=0.0, presort=False, random_state=None,
            splitter='best')

In [56]:
y_pred = classifier.predict(X_test)

In [57]:
from sklearn.metrics import mean_absolute_error
acc = 1 - mean_absolute_error(y_test, y_pred.astype(int))

acc

0.71619999999999995

In [61]:
import graphviz 
from sklearn import tree

dot_data = tree.export_graphviz(classifier, out_file=None) 
graph = graphviz.Source(dot_data) 
graph.render() 

'Source.gv.pdf'

In [62]:
graph